In [2]:
'''Columns of csv'''
STRIKE_PRICE = 'Strike Price'
CALL_LTP = 'CALL_LTP'
PUT_LTP = 'PUT_LTP'
GAMMA_CALL = 'GAMMA_CALL'

In [25]:
import os
import pandas as pd
from datetime import datetime, timedelta
import threading
from collections import defaultdict
import logging

# Configure the logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')


In [4]:
class OptionChain:
    def __init__(self):
        self.logger = logging.getLogger(__name__)
        self.start = None
        self.end = None
        self.data = defaultdict(dict)
        self.path= os.getcwd()
        self.last_stored_date = None
        self.future_date = None
        self.new_item_event = threading.Event()
        self.monitor_thread = threading.Thread(target=self.monitor_queue)
        self.monitor_thread.start()
    
    def bring_data(self,date,time,strike_price):
      
      with self.lock:
          df = self.data[date][time]
          print(df)
          filtered_df = df[df['Strike Price'] == strike_price]
          print(filtered_df)
          return filtered_df

    def __fetch_from_folder__(self, folder_path):
        if os.path.exists(folder_path):
            for file in os.listdir(folder_path):
                if file.endswith('.csv'):
                    df = pd.read_csv(os.path.join(folder_path, file))
                    date = os.path.basename(folder_path)
                    self.data[date][file] = df
        else:
            print(f"Folder {folder_path} does not exist ")
            return "", None
        return self.data, 

    def findnextdate(self,date_string):

        # Convert the string to a datetime object
        date_obj = datetime.strptime(date_string, '%Y%m%d')

        # Calculate the next date
        next_date = date_obj + timedelta(days=1)

        # Convert the next date back to string format
        next_date_string = next_date.strftime('%Y%m%d')
        return next_date_string
    
    def findprevdate(self,date_string):

        # Convert the string to a datetime object
        date_obj = datetime.strptime(date_string, '%Y%m%d')

        # Calculate the next date
        prev_date = date_obj - timedelta(days=1)

        # Convert the next date back to string format
        prev_date_string = prev_date.strftime('%Y%m%d')
        return prev_date_string
    

    #get prev 10 days and next 10 days data
    def get_data_20(self, start_date):
        if type(start_date)==str : start_date = datetime.strptime(start_date, '%Y%m%d')
        if self.last_stored_date  is None and self.future_date is None:

        if self.last_stored_date  is None : start_date
        prev_delta = start_date -  self.last_stored_date 
        # get previoud 10 th day.
        if prev_delta.days > 10: 

            while (start_date -  self.last_stored_date).days >10 :
                 del self.data[self.last_stored_date]
                 self.last_stored_date = self.last_stored_date + timedelta(days=1)
        else :
            while (start_date -  self.last_stored_date).days <10 :
                 
                 self.last_stored_date = self.last_stored_date + timedelta(days=-1)

        if (self.future_date - start_date).days < 2:

        # get next 10th day

        # print('inside get_data_20')
        # temp_dict = dict()

        # temp_date = start_date
        # dataset_path = self.path
        # subfolder_name = str(temp_date)+'\\'

        # subfolder_path = os.path.join(dataset_path, subfolder_name)

        # if os.path.exists(subfolder_path) and os.path.isdir(subfolder_path):
        #     file_names = os.listdir(subfolder_path)
        #     temp_dict[temp_date] = {}   
        #     # print("Files in subfolder:")
        #     for file_name in file_names:
        #         subfile_path = os.path.join(subfolder_path, file_name)
        #         df = pd.read_csv(subfile_path)
        #         temp_dict[start_date][file_name.split('.')[0]] = df

        # for i in range(9):
        #     temp_date = self.findprevdate(temp_date)
        #     subfolder_name = str(temp_date)+ '\\'
        #     subfolder_path = os.path.join(dataset_path, subfolder_name)

        #     if os.path.exists(subfolder_path) and os.path.isdir(subfolder_path):
        #         file_names = os.listdir(subfolder_path)
        #         temp_dict[temp_date] = {} 
        #         # print("Files in subfolder:")
        #         for file_name in file_names:
        #             subfile_path = os.path.join(subfolder_path, file_name)
        #             df = pd.read_csv(subfile_path)
        #             temp_dict[temp_date][file_name.split('.')[0]] = df
        
        # temp_date = start_date
        # for i in range(10):

        #     temp_date = self.findnextdate(temp_date)
        #     self.last_stored_date = str(temp_date)
        #     subfolder_name = str(temp_date)+'\\'
        #     subfolder_path = os.path.join(dataset_path, subfolder_name)

        #     if os.path.exists(subfolder_path) and os.path.isdir(subfolder_path):
        #         file_names = os.listdir(subfolder_path)
        #         # print("Files in subfolder:")
        #         temp_dict[temp_date] = {} 
        #         for file_name in file_names:
        #             subfile_path = os.path.join(subfolder_path, file_name)
        #             df = pd.read_csv(subfile_path)
        #             temp_dict[temp_date][file_name.split('.')[0]] = df
        
        return temp_dict
    
    def moniter_date_and_fetch_data(self):
        print('inside montior_date_and_fetch_data')

        if(self.last_stored_date ==None or self.last_fetched_date==None):
            return
        date_string1 = self.last_stored_date
        date_string2 = self.last_fetched_date

        # Convert the strings to datetime objects
        date1 = datetime.strptime(date_string1, '%Y%m%d')
        date2 = datetime.strptime(date_string2, '%Y%m%d')

        # Calculate the difference in days
        difference_in_days = (date2 - date1).days
        if  difference_in_days <=5:
            new_data = self.get_data_20(self.last_fetched_date)
            with self.lock:
                self.data = new_data


runOptionChain = OptionChain()
while True:
    
    # print(runOptionChain.data)

    date = input('ENTER DATE')
    time = input('ENTER TIME')
    if date not in runOptionChain.data:
        runOptionChain.data = runOptionChain.get_data_20(date)
    runOptionChain.last_fetched_date = date
    thread = threading.Thread(target=runOptionChain.moniter_date_and_fetch_data)
    thread.start()
    req_data = runOptionChain.bring_data(date,time, 149)
    print(req_data)





inside montior_date_and_fetch_data


inside get_data_20
inside montior_date_and_fetch_data
inside get_data_20
    Strike Price  CALL_LTP   PUT_LTP  GAMMA_CALL
0            137  6.695529  8.627095    0.145909
1            111  8.949425  4.204928    0.226340
2            118  6.742066  7.038555    0.255456
3            100  8.926340  8.111531    0.253046
4            135  5.659744  7.061651    0.275544
5            112  9.960099  8.586881    0.141808
6            108  6.024607  6.773267    0.197796
7            102  6.265893  5.323281    0.108110
8            113  8.103021  5.102398    0.267552
9            115  5.113796  8.994724    0.219692
10           105  8.006475  8.406190    0.174875
11           149  7.859677  7.278195    0.222394
12           109  9.211278  6.087418    0.135096
13           111  6.732458  5.549985    0.255895
14           136  8.428733  7.667617    0.177859
15           127  9.314123  6.608885    0.194907
16           123  8.108565  6.140384    0.244458
17           101  6.846305  5.136364    0.249

In [26]:
class OptionChain:
    def __init__(self, path) -> None:
        self.logger = logging.getLogger(__name__)
        self.data = defaultdict(dict)
        self.path= path
        self.queue = []
        self.new_item_event = threading.Event()
        self.monitor_thread = threading.Thread(target=self.monitor_queue)
        self.monitor_thread.start()

    def __fetch_from_folder__(self, folder_path):
        if os.path.exists(folder_path):
            for file in os.listdir(folder_path):
                if file.endswith('.csv'):
                    df = pd.read_csv(os.path.join(folder_path, file))
                    date = os.path.basename(folder_path)
                    self.data[date][file[:-4]] = df
        else:
            self.logger.error(f"Folder {folder_path} does not exist ")
            return "", None
        return self.data, None
    
    def monitor_queue(self):
        while True:
            if len(self.queue) == 0 :
                self.new_item_event.wait()
            for item in self.queue:
                if item in self.data :
                    continue
                self.__fetch_from_folder__(os.path.join(self.path,item))
                top = datetime.strptime(item, '%Y%m%d') - timedelta(days=20)
                if top in self.data:
                    del self.data[top]
            self.queue = []
            self.new_item_event.clear()
            
    
    def query(self, date, time, strike_price):
        query_date = datetime.strptime(date, '%Y%m%d')
        if date not in self.data :
            self.__fetch_from_folder__(os.path.join(self.path,date))
            ten_day_before = query_date - timedelta(days=10)
            while ten_day_before < query_date + timedelta(days=10) :
                folder_path =  ten_day_before.strftime("%Y%m%d") 
                self.queue.append(folder_path)
                ten_day_before = ten_day_before + timedelta(days=1)
            self.new_item_event.set()
            if date not in  self.data: return None
            return self.query(date, time, strike_price)
        else:
            if time not in self.data[date]:
                self.logger.error(f"data not present for date {date}, time {time}")
                return None
            df =  self.data[date][time]
            filtered_df = df[df[STRIKE_PRICE] == strike_price]
            if len(filtered_df) == 0 : return None
            return filtered_df.iloc[0].to_dict()
    def disable_log(self):
        self.logger.setLevel(logging.CRITICAL + 1)
    def enable_log(self, log_level):
        self.logger.setLevel(log_level)
option_chain = OptionChain("dataset")
details = option_chain.query("20240502", "0930", 116)
print(details)


{'Strike Price': 116.0, 'CALL_LTP': 5.074095627436081, 'PUT_LTP': 6.217027143615873, 'GAMMA_CALL': 0.1819107647025336}


2024-05-12 11:39:33,340 - ERROR - Folder dataset\20240422 does not exist 
2024-05-12 11:39:33,340 - ERROR - Folder dataset\20240423 does not exist 
2024-05-12 11:39:33,340 - ERROR - Folder dataset\20240424 does not exist 
2024-05-12 11:39:33,340 - ERROR - Folder dataset\20240425 does not exist 
2024-05-12 11:39:33,340 - ERROR - Folder dataset\20240426 does not exist 
2024-05-12 11:39:33,340 - ERROR - Folder dataset\20240427 does not exist 
2024-05-12 11:39:33,340 - ERROR - Folder dataset\20240428 does not exist 
2024-05-12 11:39:33,355 - ERROR - Folder dataset\20240429 does not exist 
2024-05-12 11:39:33,357 - ERROR - Folder dataset\20240430 does not exist 


2024-05-12 11:39:33,360 - ERROR - Folder dataset\20240501 does not exist 


In [1]:
{'close': 1.35, 'datetime': '2023-01-02 09:17:00', 'exchange_code': 'NFO', 'expiry_date': '05-JAN-2023', 'high': 1.4, 'low': 1.35, 'open': 1.4, 'open_interest': 51450, 'product_type': 'Options', 'right': 'Put', 'stock_code': 'NIFTY', 'strike_price': 17050.0, 'volume': 200}

{'close': 1.35,
 'datetime': '2023-01-02 09:17:00',
 'exchange_code': 'NFO',
 'expiry_date': '05-JAN-2023',
 'high': 1.4,
 'low': 1.35,
 'open': 1.4,
 'open_interest': 51450,
 'product_type': 'Options',
 'right': 'Put',
 'stock_code': 'NIFTY',
 'strike_price': 17050.0,
 'volume': 200}

In [38]:
import numpy as np
from scipy.stats import norm
from scipy.optimize import brentq
from numba import jit


def black_scholes_call(S, K, T, r, sigma):
    """Calculate the Black-Scholes price for a European call option."""
    d1 = (np.log(S / K) + (r + 0.5 * sigma ** 2) * T) / (sigma * np.sqrt(T))
    d2 = d1 - sigma * np.sqrt(T)
    call_price = S * norm.cdf(d1) - K * np.exp(-r * T) * norm.cdf(d2)
    return call_price

def black_scholes_put(S, K, T, r, sigma):
    """Calculate the Black-Scholes price for a European put option."""
    d1 = (np.log(S / K) + (r + 0.5 * sigma ** 2) * T) / (sigma * np.sqrt(T))
    d2 = d1 - sigma * np.sqrt(T)
    put_price = K * np.exp(-r * T) * norm.cdf(-d2) - S * norm.cdf(-d1)
    return put_price

def implied_volatility(market_price, S, K, T, r, option_type='call'):
    """Calculate the implied volatility using the Black-Scholes model."""
    if option_type == 'call':
        price_function = black_scholes_call
    elif option_type == 'put':
        price_function = black_scholes_put
    else:
        raise ValueError("option_type must be 'call' or 'put'")
    
    def objective_function(sigma):
        return price_function(S, K, T, r, sigma) - market_price
    
    # Use Brent's method to solve for implied volatility
    implied_vol = brentq(objective_function, 0.01, 3.0)
    return implied_vol

# Example usage
S = 22957.10        # Current price of Nifty
K = 22950        # Strike price of the option
T = 6/365          # Time to expiry in years (3 days in this case)
r = 0.067          # Risk-free interest rate (5% annualized)
market_price = 183  # Current market price of the option

iv_call = implied_volatility(market_price, S, K, T, r, option_type='call')
iv_put = implied_volatility(market_price, S, K, T, r, option_type='put')

print(f"Implied Volatility (Call): {iv_call}")

Implied Volatility (Call): 0.14174081092616603


In [35]:
from collections import defaultdict
import pickle
nifty_call_data = defaultdict(dict)
def add_to_stock(strike_price, sample_data, security_type):
    for f in os.listdir(security_type):
        if str(f).endswith('pickle'):
            with open(f, 'rb') as r:
                data = pickle.load(r)
                # for data in sample_data:
                #     date = datetime.strptime(data['datetime'],"%Y-%m-%d %H:%M:%S")
                #     nifty_call_data[date][strike_price]={security_type: data['close']}


2024-05-06 11:32:00
2024-05-06 11:33:00
2024-05-06 11:34:00
2024-05-06 11:35:00
2024-05-06 11:36:00
2024-05-06 11:37:00
2024-05-06 11:38:00
2024-05-06 11:39:00
2024-05-06 11:40:00
2024-05-06 11:41:00
2024-05-06 11:42:00
2024-05-06 11:43:00


In [29]:
import  mibian
from numba import njit

def get_greeks(underlying_price, strike_price, LTP, days_to_expiry, intrest_rate, right):
    if right =='call':
        bs = mibian.BS([underlying_price,strike_price,intrest_rate, days_to_expiry],callPrice= LTP)
    else :
        bs = mibian.BS([underlying_price,strike_price,intrest_rate, days_to_expiry],PutPrice= LTP)
    v = bs.impliedVolatility
    bs = mibian.BS([underlying_price,strike_price,intrest_rate, days_to_expiry], v)
    if right == 'call':
        return bs.callDelta, bs.gamma, bs.callTheta, bs.vega
    else:
        return bs.putDelta, bs.gamma, bs.putTheta, bs.vega 
    

In [48]:
limit = len(nifty_call_data)-1
limit

20559

In [49]:
import pickle, os
from collections import defaultdict
from datetime import datetime
import mibian
from tqdm import tqdm
with open('nifty_data.picke', 'rb') as data:
         nifty = pickle.load(data)
# security_type='call'
intrest_rate=6.75

# nifty_call_data = defaultdict(lambda : defaultdict(dict))
limit = len(nifty_call_data)-1
i=0
sec= ['call', 'put']
for security_type in sec:
    for f in tqdm(os.listdir(security_type)):
            
            if str(f).endswith('pickle'):
                with open(security_type+'\\'+f, 'rb') as r:
                    data_list = pickle.load(r)
                    for record in data_list:
                        sample_data = record['data']
                        for data in sample_data:
                            # if i < limit:
                            #     i+=1
                            #     continue
                            strike_price = data['strike_price']
                            date = datetime.strptime(data['datetime'],"%Y-%m-%d %H:%M:%S")
                            expiry_date = datetime.strptime(data['expiry_date'], '%d-%b-%Y')
                            days_to_expiry = (expiry_date - date).days + 1
                            price = data['close']
                            if date not in nifty:
                                 print(date, "not in nifty")
                                 continue
                            if price == 0 :
                                 print(data, "price is zero")
                                 continue
                            underlying_price = nifty[date]
                            if date in nifty_call_data and security_type in nifty_call_data[date] and strike_price in nifty_call_data[date][security_type] :
                                 continue 
                            try: 
                                delta, gamma, theta, vega = get_greeks(underlying_price, strike_price, price, days_to_expiry, intrest_rate, security_type)
                                # print(delta, gamma, theta, vega)
                            except Exception as e:
                                 print(data, e)
                            nifty_call_data[date][security_type][strike_price]=data
                            nifty_call_data[date][security_type][strike_price]['delta'] = delta
                            nifty_call_data[date][security_type][strike_price]['gamma'] = gamma
                            nifty_call_data[date][security_type][strike_price]['theta'] = theta
                            nifty_call_data[date][security_type][strike_price]['vega'] = vega

                    # nifty_call_data[date][strike_price]={security_type: data}

  1%|          | 6/618 [00:00<00:13, 45.17it/s]

2023-01-09 09:20:00 not in nifty
2023-01-09 10:06:00 not in nifty
2023-01-09 10:49:00 not in nifty
2023-01-09 09:20:00 not in nifty
2023-01-09 09:25:00 not in nifty
2023-01-09 11:13:00 not in nifty
2023-01-09 11:14:00 not in nifty
2023-01-23 09:24:00 not in nifty
2023-01-23 09:26:00 not in nifty
2023-01-23 09:27:00 not in nifty
2023-01-23 09:44:00 not in nifty
2023-01-23 10:21:00 not in nifty
2023-01-23 10:22:00 not in nifty
2023-01-23 10:32:00 not in nifty
2023-01-09 09:20:00 not in nifty
2023-01-09 09:25:00 not in nifty
2023-01-09 09:20:00 not in nifty
2023-01-09 09:24:00 not in nifty
2023-01-09 09:25:00 not in nifty
2023-01-09 09:26:00 not in nifty
2023-01-09 09:27:00 not in nifty
2023-01-09 09:29:00 not in nifty
2023-01-09 09:30:00 not in nifty
2023-01-09 09:31:00 not in nifty
2023-01-09 09:35:00 not in nifty
2023-01-09 09:36:00 not in nifty
2023-01-09 09:39:00 not in nifty
2023-01-09 09:43:00 not in nifty
2023-01-09 09:55:00 not in nifty
2023-01-09 10:05:00 not in nifty
2023-01-09

  2%|▏         | 11/618 [00:00<00:30, 19.99it/s]

2023-01-09 09:16:00 not in nifty
2023-01-09 09:17:00 not in nifty
2023-01-09 09:18:00 not in nifty
2023-01-09 09:19:00 not in nifty
2023-01-09 09:20:00 not in nifty
2023-01-09 09:21:00 not in nifty
2023-01-09 09:23:00 not in nifty
2023-01-09 09:24:00 not in nifty
2023-01-09 09:25:00 not in nifty
2023-01-09 09:26:00 not in nifty
2023-01-09 09:27:00 not in nifty
2023-01-09 09:29:00 not in nifty
2023-01-09 09:30:00 not in nifty
2023-01-09 09:31:00 not in nifty
2023-01-09 09:32:00 not in nifty
2023-01-09 09:33:00 not in nifty
2023-01-09 09:34:00 not in nifty
2023-01-09 09:35:00 not in nifty
2023-01-09 09:36:00 not in nifty
2023-01-09 09:37:00 not in nifty
2023-01-09 09:38:00 not in nifty
2023-01-09 09:39:00 not in nifty
2023-01-09 09:40:00 not in nifty
2023-01-09 09:41:00 not in nifty
2023-01-09 09:42:00 not in nifty
2023-01-09 09:43:00 not in nifty
2023-01-09 09:44:00 not in nifty
2023-01-09 09:45:00 not in nifty
2023-01-09 09:47:00 not in nifty
2023-01-09 09:49:00 not in nifty
2023-01-09

  2%|▏         | 14/618 [00:00<00:46, 12.99it/s]

...

2023-02-28 09:16:00 not in nifty
2023-02-28 09:17:00 not in nifty
2023-02-28 09:18:00 not in nifty
2023-02-28 09:19:00 not in nifty
2023-02-28 09:20:00 not in nifty
2023-02-28 09:21:00 not in nifty
2023-02-28 09:22:00 not in nifty
2023-02-28 09:23:00 not in nifty
2023-02-28 09:24:00 not in nifty
2023-02-28 09:25:00 not in nifty
2023-02-28 09:26:00 not in nifty
2023-02-28 09:27:00 not in nifty
2023-02-28 09:28:00 not in nifty
2023-02-28 09:29:00 not in nifty
2023-02-28 09:30:00 not in nifty
2023-02-28 09:31:00 not in nifty
2023-02-28 09:32:00 not in nifty
2023-02-28 09:33:00 not in nifty
2023-02-28 09:34:00 not in nifty
2023-02-28 09:35:00 not in nifty
2023-02-28 09:36:00 not in nifty
2023-02-28 09:37:00 not in nifty
2023-02-28 09:38:00 not in nifty
2023-02-28 09:39:00 not in nifty
2023-02-28 09:40:00 not in nifty
2023-02-28 09:41:00 not in nifty
2023-02-28 09:42:00 not in nifty
2023-02-28 09:43:00 not in nifty
2023-02-28 09:44:00 not in nifty
2023-02-28 09:45:00 not in nifty
2023-02-28

 17%|█▋        | 102/618 [7:28:25<11:32:51, 80.57s/it]

{'close': 165.45, 'datetime': '2023-03-29 09:16:00', 'exchange_code': 'NFO', 'expiry_date': '29-MAR-2023', 'high': 168.95, 'low': 159.25, 'open': 159.75, 'open_interest': 489100, 'product_type': 'Options', 'right': 'Call', 'stock_code': 'NIFTY', 'strike_price': 16850.0, 'volume': 108900} float division by zero
{'close': 170.05, 'datetime': '2023-03-29 09:17:00', 'exchange_code': 'NFO', 'expiry_date': '29-MAR-2023', 'high': 174.45, 'low': 165.45, 'open': 165.45, 'open_interest': 509150, 'product_type': 'Options', 'right': 'Call', 'stock_code': 'NIFTY', 'strike_price': 16850.0, 'volume': 107500} float division by zero
{'close': 167.25, 'datetime': '2023-03-29 09:18:00', 'exchange_code': 'NFO', 'expiry_date': '29-MAR-2023', 'high': 173.35, 'low': 165.0, 'open': 170.85, 'open_interest': 509150, 'product_type': 'Options', 'right': 'Call', 'stock_code': 'NIFTY', 'strike_price': 16850.0, 'volume': 85600} float division by zero
{'close': 159.2, 'datetime': '2023-03-29 09:19:00', 'exchange_code

 17%|█▋        | 102/618 [8:04:58<40:53:22, 285.28s/it]


KeyboardInterrupt: 

In [31]:
nifty_call_data

defaultdict(<function __main__.<lambda>()>,
            {datetime.datetime(2023, 1, 2, 15, 18): defaultdict(dict,
                         {'call': {17050.0: {'close': 1161.75,
                            'datetime': '2023-01-02 15:18:00',
                            'exchange_code': 'NFO',
                            'expiry_date': '05-JAN-2023',
                            'high': 1161.75,
                            'low': 1153.55,
                            'open': 1153.55,
                            'open_interest': 500,
                            'product_type': 'Options',
                            'right': 'Call',
                            'stock_code': 'NIFTY',
                            'strike_price': 17050.0,
                            'volume': 1150,
                            'delta': 0.9903559090593612,
                            'gamma': 5.010121271969463e-05,
                            'theta': -5.336616162349602,
                            'vega': 0.426074

In [34]:
import dill
with open('nested_defaultdict.pkl', 'wb') as f:
    dill.dump(nifty_call_data, f)

In [41]:

!pip install dill


  Using cached dill-0.3.8-py3-none-any.whl.metadata (10 kB)
Using cached dill-0.3.8-py3-none-any.whl (116 kB)


In [50]:
import dill
with open("nifty_chain.dill",'wb') as g:
    dill.dump(nifty_call_data,g)

In [30]:
len(nifty)

122366

In [36]:
date

datetime.datetime(2023, 1, 25, 12, 21)

In [ ]:
date_custom = datetime(2023,1,2,12,26,0) + timedelta(minutes=1)

In [37]:
strike_price

17400.0

In [40]:
date_custom = datetime(2023,1,2,12,26,0) 
security_type = 'call'
strike_price = 17300.0
nifty_call_data[date_custom][security_type][strike_price]

KeyError: 17300.0

In [51]:
nifty_call_data[datetime(2023, 1, 2, 15, 18)]['call'][17050.0]

{'close': 1161.75,
 'datetime': '2023-01-02 15:18:00',
 'exchange_code': 'NFO',
 'expiry_date': '05-JAN-2023',
 'high': 1161.75,
 'low': 1153.55,
 'open': 1153.55,
 'open_interest': 500,
 'product_type': 'Options',
 'right': 'Call',
 'stock_code': 'NIFTY',
 'strike_price': 17050.0,
 'volume': 1150,
 'delta': None,
 'gamma': None,
 'theta': None,
 'vega': None}

In [21]:
nifty[date]

17899.85

In [18]:
data

<_io.BufferedReader name='nifty_data.picke'>

In [3]:
import mibian

In [35]:
underlying_price = 22957.10
call_strike = 22950
# put_strike = 22100
call_price = 183
# put_price=162.75
intrest_rate = 6.75
days_to_expiry = 6

bs = mibian.BS([underlying_price,call_strike,intrest_rate, days_to_expiry], callPrice=call_price )
print(bs.impliedVolatility)
bs = mibian.BS([underlying_price,call_strike,intrest_rate, days_to_expiry], bs.impliedVolatility )
# days_to_expiry = 4
print(f'call_delta: {bs.callDelta}, gamma: {bs.gamma}, theta: {bs.callTheta}, vega: {bs.vega}')
print(get_greeks(underlying_price, call_strike, call_price, days_to_expiry, intrest_rate, "call" ))
# bs = mibian.BS([underlying_price,call_strike,intrest_rate, days_to_expiry], call_price)
# print(f'call_delta: {bs.callDelta}, gamma: {bs.gamma}, theta: {bs.callTheta}, vega: {bs.vega}')

14.16778564453125
call_delta: 0.5347419191765314, gamma: 0.0009530394740706342, theta: -16.047423790469246, vega: 11.69782996868747
(0.5347419191765314, 0.0009530394740706342, -16.047423790469246, 11.69782996868747)


call_delta: 0.5397850738117579, gamma: 9.117907325741548e-05, theta: -144.01579269774095, vega: 11.224925385638423
